In [10]:
import json
import numpy as np
import hnswlib
import networkx as nx
from collections import defaultdict

## Reading Embeddings and creating Indexer for NN search

In [2]:
IDList = []                                # List of paper IDs
NNList = []                                # List of list, NNList[i]: NNs to paper whose id is IDList[i]
embeddings = []                            # Embeddings read from the input file

with open('./data/dblpAbstract_2Thresholded_FT_Embeddings.json', 'r') as file:
    for line in file:
        data = json.loads(line)
        paperID = data['id']
        embedding = data['embedding']
        IDList.append(paperID)
        embeddings.append(embedding)

In [3]:
numElements = len(IDList)
dimension = len(embeddings[0])
embeddings = np.asarray(embeddings)
data_labels = np.arange(numElements)

## Create a new Indexer and save it 

In [ ]:
p = hnswlib.Index(space = 'cosine', dim = dimension) # possible options are l2, cosine or ip

# Initing index - the maximum number of elements should be known beforehand
p.init_index(max_elements = numElements, ef_construction = 200, M = 20)

# Element insertion (can be called several times):
p.add_items(embeddings, data_labels)

# Controlling the recall by setting ef:
p.set_ef(50) # ef should always be > k

# Query dataset, k - number of closest elements (returns 2 numpy arrays)
labels, _ = p.knn_query(embeddings, k = 5)

In [ ]:
index_path='./models/fastTexthnswlib.bin'
print("Saving index to '%s'" % index_path)
p.save_index("./models/fastTexthnswlib.bin")
del p

## Load a built Indexer

In [4]:
p = hnswlib.Index(space='cosine', dim=dimension)  # the space can be changed - keeps the data, alters the distance function.

# Increase the total capacity (max_elements), so that it will handle the new data
p.load_index("./models/fastTexthnswlib.bin", max_elements = numElements)
labels, _ = p.knn_query(embeddings, k = 4)
del p

## Examples of NN obtained using the Text Embeddings

In [ ]:
titles = []
with open('./data/dblp_AIpapers2Thresholded.json', 'r') as file:
    for line in file:
        data = json.loads(line)
        titles.append(data['title'])

In [ ]:
count = 5
for i in range(count):
    print('Paper: ', titles[i])
    print('Nearest Papers: ', [titles[ind] for ind in labels[i] if ind != i])
    print('\n')

## Building Adjacency List for Node Embeddings

### Creating Citation Adjacency List

In [24]:
adjList = defaultdict(set)                          # Convert set to list later for node2vec, set: to handle duplicates
citationThreshold = 2
count = 0
PapersOutFileName = './data/dblp_AIpapers' + str(citationThreshold) + 'Thresholded.json'
with open(PapersOutFileName, 'r') as file:
    for line in file:
        count +=1
        data = json.loads(line)
        paperID = data['id']
        if (paperID == '100838754'):
            print('FOUND')
        references = data.get('references', [])
        for referencedPaper in references:
            adjList[paperID].add(referencedPaper)
            adjList[referencedPaper].add(paperID)

FOUND


### Augmenting Adj List with FastText NNs

In [6]:
nnToKeep = 3
id = 0
for label in labels:
    paperID = IDList[id]
    label = [IDList[index] for index in label if index != id]
    if (len(label) > nnToKeep):
        del label[nnToKeep:]
    for referencedPaper in label:
        adjList[paperID].add(referencedPaper)
        adjList[referencedPaper].add(paperID)
    id += 1

### Creating NetworkX Graph and reporting graph statistics

In [12]:
adjList = {key: list(values) for key, values in adjList.items()}
G = nx.from_dict_of_lists(adjList)

nnodes = G.number_of_nodes()
avgDegree = sum(d for n, d in G.degree()) / float(nnodes)
print('Number of nodes: ', nnodes, '. Number of edges: ', G.number_of_edges(), '. Avg Degree: ', avgDegree)

Number of nodes:  471633 . Number of edges:  5464345 . Avg Degree:  23.172021465843144


## Node2Vec Embeddings

In [13]:
from node2vec import Node2Vec
node2vec = Node2Vec(G, walk_length = 6) #, workers = 12,  temp_folder = './data/tmp_data2')



Computing transition probabilities:   0%|          | 416/471633 [00:28<28:43:15,  4.56it/s]


Computing transition probabilities:   0%|          | 929/471633 [00:51<3:39:37, 35.72it/s]


Computing transition probabilities:   0%|          | 1413/471633 [01:11<8:18:04, 15.73it/s]


Computing transition probabilities:   0%|          | 1851/471633 [01:31<13:22:12,  9.76it/s]


Computing transition probabilities:   0%|          | 2262/471633 [01:52<7:30:49, 17.35it/s]


...

Computing transition probabilities:  99%|█████████▉| 468944/471633 [1:49:54<01:12, 37.31it/s]


Computing transition probabilities: 100%|█████████▉| 469442/471633 [1:50:05<00:53, 41.25it/s]


Computing transition probabilities: 100%|█████████▉| 469978/471633 [1:50:16<00:33, 50.07it/s]


Computing transition probabilities: 100%|█████████▉| 470883/471633 [1:50:29<00:12, 61.40it/s]


Generating walks (CPU: 1): 100%|██████████| 10/10 [40:19<00:00, 260.30s/it]

In [14]:
model = node2vec.fit()              # returns a gensim wv model

In [15]:
model.wv.save_word2vec_format('./models/node2vec_Embeddings.kv')

In [16]:
model.wv['100838754']

KeyError: "word '100838754' not in vocabulary"

In [17]:
'100838754' in adjList.keys()

False

In [22]:
len(adjList.keys())

471633

In [23]:
count

475839